In [1]:
# 读取配置
# 父目录下的lib
from lib.dataread import *
from lib.tools import Graphs,mse,rmse,mae,exception_logger



数据库连接成功 192.168.101.27 jingbo_test root


In [7]:

# 原油计算预测评估指数
@exception_logger
def model_losss(sqlitedb,end_time):
    global dataset
    global rote
    most_model = [sqlitedb.select_data('most_model',columns=['most_common_model'],order_by='ds desc',limit=1).values[0][0]]
    most_model_name = most_model[0]

    # 预测数据处理 predict
    df_combined = loadcsv(os.path.join(dataset,"cross_validation.csv"))  
    df_combined = dateConvert(df_combined)
    # 删除空列
    df_combined.dropna(axis=1,inplace=True)
     # 删除缺失值,预测过程不能有缺失值
    df_combined.dropna(inplace=True) 
    # 其他列转为数值类型
    df_combined = df_combined.astype({col: 'float32' for col in df_combined.columns if col not in ['cutoff','ds'] })
    # 使用 groupby 和 transform 结合 lambda 函数来获取每个分组中 cutoff 的最小值，并创建一个新的列来存储这个最大值
    df_combined['max_cutoff'] = df_combined.groupby('ds')['cutoff'].transform('max')

    # 然后筛选出那些 cutoff 等于 max_cutoff 的行，这样就得到了每个分组中 cutoff 最大的行，并保留了其他列
    df_combined = df_combined[df_combined['cutoff'] == df_combined['max_cutoff']]
    # 删除模型生成的cutoff列
    df_combined.drop(columns=['cutoff', 'max_cutoff'], inplace=True)
    # 获取模型名称
    modelnames  = df_combined.columns.to_list()[1:] 
    if 'y' in modelnames:
        modelnames.remove('y')
    # df_combined3 = df_combined.copy()  # 备份df_combined,后面画图需要
    df_combined3 = sqlitedb.select_data('accuracy')


    # 空的列表存储每个模型的MSE、RMSE、MAE、MAPE、SMAPE
    cellText = []

    # 遍历模型名称，计算模型评估指标  
    for model in modelnames:
        modelmse = mse(df_combined['y'], df_combined[model])
        modelrmse = rmse(df_combined['y'], df_combined[model])
        modelmae = mae(df_combined['y'], df_combined[model])
        # modelmape = mape(df_combined['y'], df_combined[model])
        # modelsmape = smape(df_combined['y'], df_combined[model])
        # modelr2 = r2_score(df_combined['y'], df_combined[model])
        cellText.append([model,round(modelmse, 3), round(modelrmse, 3), round(modelmae, 3)])
        
    model_results3 = pd.DataFrame(cellText,columns=['模型(Model)','平均平方误差(MSE)', '均方根误差(RMSE)',  '平均绝对误差(MAE)'])
    # 按MSE降序排列
    model_results3 = model_results3.sort_values(by='平均平方误差(MSE)', ascending=True)
    model_results3.to_csv(os.path.join(dataset,"model_evaluation.csv"),index=False)
    modelnames = model_results3['模型(Model)'].tolist()
    allmodelnames = modelnames.copy()
    # # 保存5个最佳模型的名称
    # if len(modelnames) > 5:
    #     modelnames = modelnames[0:5]
    # if is_fivemodels:
    #     pass
    # else:
    #     with open(os.path.join(dataset,"best_modelnames.txt"), 'w') as f:
    #         f.write(','.join(modelnames) + '\n')

    # # 预测值与真实值对比图
    # plt.rcParams['font.sans-serif'] = ['SimHei']
    # plt.figure(figsize=(15, 10))
    # for n,model in enumerate(modelnames[:5]):
    #     plt.subplot(3, 2, n+1)
    #     plt.plot(df_combined3['ds'], df_combined3['y'], label='真实值')
    #     plt.plot(df_combined3['ds'], df_combined3[model], label=model)
    #     plt.legend()
    #     plt.xlabel('日期')
    #     plt.ylabel('价格')
    #     plt.title(model+'拟合')
    # plt.subplots_adjust(hspace=0.5)
    # plt.savefig(os.path.join(dataset,'预测值与真实值对比图.png'), bbox_inches='tight')
    # plt.close()
    
    
    # # 历史数据+预测数据
    # # 拼接未来时间预测
    df_predict  = pd.read_csv(os.path.join(dataset,'predict.csv'))
    df_predict.drop('unique_id',inplace=True,axis=1)
    df_predict.dropna(axis=1,inplace=True)

    try:
        df_predict['ds'] = pd.to_datetime(df_predict['ds'],format=r'%Y-%m-%d')
    except ValueError :
        df_predict['ds'] = pd.to_datetime(df_predict['ds'],format=r'%Y/%m/%d')

    
    df_combined3 = pd.concat([df_combined3, df_predict]).reset_index(drop=True)

    # 计算每个模型与最佳模型的绝对误差比例，根据设置的阈值rote筛选预测值显示最大最小值
    # names = []
    # names_df = df_combined3.copy()
    # for col in allmodelnames:
    #     names_df[f'{col}-{most_model_name}-误差比例'] = abs(names_df[col] - names_df[most_model_name]) / names_df[most_model_name]
    #     names.append(f'{col}-{most_model_name}-误差比例')

    # names_df = names_df[names]
    # def add_rote_column(row):
    #     columns = []
    #     for r in names_df.columns:
    #         if row[r] <= rote:
    #             columns.append(r.split('-')[0])
    #     return pd.Series([columns], index=['columns'])
    # names_df['columns'] = names_df.apply(add_rote_column, axis=1)
    
    def add_upper_lower_bound(row):

        # 计算上边界值
        upper_bound = row.max()
        # 计算下边界值
        lower_bound = row.min()
        return pd.Series([lower_bound, upper_bound], index=['min_within_quantile', 'max_within_quantile'])

    # df_combined3[['min_within_quantile','max_within_quantile']] = names_df.apply(add_upper_lower_bound, axis=1)

    # 取前五最佳模型的最大最小值作为上下边界值
    # df_combined3[['min_within_quantile','max_within_quantile']]= df_combined3[modelnames].apply(add_upper_lower_bound, axis=1)
    
    def find_closest_values(row):
        x = row.y
        if x is None or np.isnan(x):
            return pd.Series([None, None], index=['min_price','max_price'])
        # row = row.drop('ds')
        row = row.values.tolist()
        row.sort()
        print(row)
        # x 在row中的索引
        index = row.index(x)
        if index == 0:
            return pd.Series([row[index+1], row[index+2]], index=['min_price','max_price'])
        elif index == len(row)-1:
            return pd.Series([row[index-2], row[index-1]], index=['min_price','max_price'])
        else:
            return pd.Series([row[index-1], row[index+1]], index=['min_price','max_price'])


    
    def find_most_common_model():
        # 最多频率的模型名称
        min_model_max_frequency_model = df_combined3['min_model'].tail(60).value_counts().idxmax()
        max_model_max_frequency_model = df_combined3['max_model'].tail(60).value_counts().idxmax()
        if min_model_max_frequency_model == max_model_max_frequency_model:
            # 取60天第二多的模型
            max_model_max_frequency_model = df_combined3['max_model'].tail(60).value_counts().nlargest(2).index[1]

        df_predict['min_model'] = min_model_max_frequency_model
        df_predict['max_model'] = max_model_max_frequency_model
        df_predict['min_within_quantile'] = df_predict[min_model_max_frequency_model]
        df_predict['max_within_quantile'] = df_predict[max_model_max_frequency_model]


    # find_most_common_model()

    df_combined3['ds'] = pd.to_datetime(df_combined3['ds'])
    df_combined3['ds'] = df_combined3['ds'].dt.strftime('%Y-%m-%d')
    df_predict2 = df_combined3.tail(horizon)

    # 保存到数据库
    # if not sqlitedb.check_table_exists('accuracy'):
    #     columns = ','.join(df_combined3.columns.to_list()+['id','CREAT_DATE','min_price','max_price'])
    #     sqlitedb.create_table('accuracy',columns=columns)
    # existing_data = sqlitedb.select_data(table_name = "accuracy")

    # if  not existing_data.empty:
    #     max_id = existing_data['id'].astype(int).max()
    #     df_predict2['id'] = range(max_id + 1, max_id + 1 + len(df_predict2))
    # else:
    #     df_predict2['id'] = range(1, 1 + len(df_predict2))
    # df_predict2['CREAT_DATE'] = now if end_time == '' else end_time
    # df_predict2['CREAT_DATE'] = end_time
    # def get_common_columns(df1, df2):
    #     # 获取两个DataFrame的公共列名
    #     return list(set(df1.columns).intersection(df2.columns))

    # common_columns = get_common_columns(df_predict2, existing_data)
    # try:
    #     df_predict2[common_columns].to_sql("accuracy",  con=sqlitedb.connection, if_exists='append', index=False)
    # except:
    #     df_predict2.to_sql("accuracy",  con=sqlitedb.connection, if_exists='append', index=False)
    
    # 更新accuracy表中的y值
    # update_y = sqlitedb.select_data(table_name = "accuracy",where_condition='y is null')
    # if len(update_y) > 0:
    #     df_combined4 = df_combined3[(df_combined3['ds'].isin(update_y['ds'])) & (df_combined3['y'].notnull())]
    #     if len(df_combined4) > 0:            
    #         for index, row in df_combined4.iterrows():
    #             try:
    #                 sqlitedb.update_data('accuracy',f"y = {row['y']}",f"ds = '{row['ds']}'")
    #             except:
    #                 logger.error(f'更新accuracy表中的y值失败，row={row}')
    # 上周准确率计算
    # predict_y = sqlitedb.select_data(table_name = "accuracy") 
    # ids = predict_y[predict_y['min_price'].isnull()]['id'].tolist()
    # ids = predict_y['id'].tolist()
    # 准确率基准与绘图上下界逻辑一致
    # predict_y[['min_price','max_price']] = predict_y[['min_within_quantile','max_within_quantile']]
    # 模型评估前五均值      
    # predict_y['min_price'] = predict_y[modelnames].mean(axis=1) -1
    # predict_y['max_price'] = predict_y[modelnames].mean(axis=1) +1
    # # 模型评估前十均值      
    # predict_y['min_price'] = predict_y[allmodelnames[0:10]].mean(axis=1) -1.5
    # predict_y['max_price'] = predict_y[allmodelnames[0:10]].mean(axis=1) +1.5
    # 模型评估前十最大最小
    # allmodelnames 和 predict_y 列 重复的
    # allmodelnames = [col for col in allmodelnames if col in predict_y.columns]
    # predict_y['min_price'] = predict_y[allmodelnames[0:10]].min(axis=1) 
    # predict_y['max_price'] = predict_y[allmodelnames[0:10]].max(axis=1)
    # for id in ids:
    #     row = predict_y[predict_y['id'] == id]
    #     try:
    #         sqlitedb.update_data('accuracy',f"min_price = {row['min_price'].values[0]},max_price = {row['max_price'].values[0]}",f"id = {id}")
    #     except:
    #         logger.error(f'更新accuracy表中的min_price,max_price值失败，row={row}')
    # 拼接市场最高最低价
    # xlsfilename = os.path.join(dataset,'数据项下载.xls')
    # df2 = pd.read_excel(xlsfilename)[5:]
    # df2 = df2.rename(columns = {'数据项名称':'ds','布伦特最低价':'LOW_PRICE','布伦特最高价':'HIGH_PRICE'})
    # print(df2.shape)
    # df = pd.merge(predict_y,df2,on=['ds'],how='left')
    # df['ds'] =  pd.to_datetime(df['ds'])
    # df = df.reindex()

    # 判断预测值在不在布伦特最高最低价范围内，准确率为1，否则为0
    # def is_within_range(row):
    #     for model in allmodelnames:
    #         if row['LOW_PRICE'] <= row[col] <= row['HIGH_PRICE']:
    #             return 1
    #     else:
    #         return 0

    # 比较真实最高最低，和预测最高最低 计算准确率
    # def calculate_accuracy(row):
    #     # 全子集情况：
    #     if (row['max_price'] >= row['HIGH_PRICE'] and row['min_price'] <= row['LOW_PRICE']) or \
    #         (row['max_price'] <= row['HIGH_PRICE'] and row['min_price'] >= row['LOW_PRICE']):
    #         return 1    
    #     # 无交集情况：
    #     if row['max_price'] < row['LOW_PRICE'] or \
    #         row['min_price'] > row['HIGH_PRICE']:
    #         return 0
    #     # 有交集情况：
    #     else:
    #         sorted_prices = sorted([row['LOW_PRICE'], row['min_price'], row['max_price'], row['HIGH_PRICE']])
    #         middle_diff = sorted_prices[2] - sorted_prices[1]
    #         price_range = row['HIGH_PRICE'] - row['LOW_PRICE']
    #         accuracy = middle_diff / price_range
    #         return accuracy

    # columns = ['HIGH_PRICE','LOW_PRICE','min_price','max_price']
    # df[columns] = df[columns].astype(float)
    # df['ACCURACY'] = df.apply(calculate_accuracy, axis=1)
    # df['ACCURACY'] = df.apply(is_within_range, axis=1)
    # 取结束日期上一周的日期
    def get_week_date(end_time):
        endtime = end_time
        endtimeweek = datetime.datetime.strptime(endtime, '%Y-%m-%d')
        up_week = endtimeweek - datetime.timedelta(days=endtimeweek.weekday() + 14)
        up_week_dates = [up_week + datetime.timedelta(days=i) for i in range(14)]
        create_dates = [date.strftime('%Y-%m-%d') for date in up_week_dates[4:-3]]
        ds_dates = [date.strftime('%Y-%m-%d') for date in up_week_dates[-7:-2]]
        return create_dates,ds_dates
    
    create_dates,ds_dates = get_week_date(end_time)
    # 计算准确率并保存结果
    def _get_accuracy_rate(df,create_dates,ds_dates):
        df3 = df.copy()
        df3 = df3[df3['CREAT_DATE'].isin(create_dates)]
        df3 = df3[df3['ds'].isin(ds_dates)]
        accuracy_rote = 0
        for i,group in df3.groupby('CREAT_DATE'):
            accuracy_rote += (group['ACCURACY'].sum()/len(group))*weight_dict[len(group)-1]
        df4 = pd.DataFrame(columns=['开始日期','结束日期','准确率'])
        df4.loc[len(df4)] = {'开始日期':ds_dates[0],'结束日期':ds_dates[-1],'准确率':accuracy_rote}
        df4.to_sql("accuracy_rote",  con=sqlitedb.connection, if_exists='append', index=False)
        # return df4
    
    # _get_accuracy_rate(df,create_dates,ds_dates)
    
    def _add_abs_error_rate():
        # 计算每个预测值与真实值之间的偏差率
        for model in allmodelnames:
            df_combined3[f'{model}_abs_error_rate'] = abs(df_combined3['y'] - df_combined3[model]) / df_combined3['y']

        # 获取每行对应的最小偏差率值
        min_abs_error_rate_values = df_combined3.apply(lambda row: row[[f'{model}_abs_error_rate' for model in allmodelnames]].min(), axis=1)
        # 获取每行对应的最小偏差率值对应的列名
        min_abs_error_rate_column_name = df_combined3.apply(lambda row: row[[f'{model}_abs_error_rate' for model in allmodelnames]].idxmin(), axis=1) 
        # 将列名索引转换为列名
        min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
        # 获取最小偏差率对应的模型的预测值
        min_abs_error_rate_predictions = df_combined3.apply(lambda row: row[min_abs_error_rate_column_name[row.name]], axis=1)
        # 将最小偏差率对应的模型的预测值添加到DataFrame中
        df_combined3['min_abs_error_rate_prediction'] = min_abs_error_rate_predictions
        df_combined3['min_abs_error_rate_column_name'] = min_abs_error_rate_column_name
    _add_abs_error_rate()

    # 判断 df 的数值列转为float
    for col in df_combined3.columns:
        try:
            if col != 'ds':
                df_combined3[col] = df_combined3[col].astype(float)
                df_combined3[col] = df_combined3[col].round(2)
        except ValueError:
            pass
    df_combined3.to_csv(os.path.join(dataset,"testandpredict_groupby.csv"),index=False) 
    
    
     # 历史价格+预测价格
    sqlitedb.drop_table('testandpredict_groupby')
    df_combined3.to_sql('testandpredict_groupby',sqlitedb.connection,index=False)
    # 新增均值列
    df_combined3['mean'] = df_combined3[modelnames].mean(axis=1)

    # def _plt_predict_ture(df):
    #     lens = df.shape[0] if df.shape[0] < 180 else 90
    #     df = df[-lens:] # 取180个数据点画图
    #     # 历史价格
    #     plt.figure(figsize=(20, 10))
    #     plt.plot(df['ds'], df['y'], label='真实值')
    #     # 均值线
    #     plt.plot(df['ds'], df['mean'], color='r', linestyle='--', label='前五模型预测均值')
    #     # 颜色填充
    #     plt.fill_between(df['ds'], df['max_within_quantile'], df['min_within_quantile'], alpha=0.2)
    #     markers = ['o', 's', '^', 'D', 'v', '*', 'p', 'h', 'H', '+', 'x', 'd']
    #     random_marker = random.choice(markers)
    #     for model in modelnames:
    #     # for model in ['BiTCN','RNN']:
    #         plt.plot(df['ds'][-horizon:], df[model][-horizon:], label=model,marker=random_marker)
    #     # plt.plot(df_combined3['ds'], df_combined3['min_abs_error_rate_prediction'], label='最小绝对误差', linestyle='--', color='orange')
    #     # 网格
    #     plt.grid(True)
    #     # 显示历史值
    #     for i, j in zip(df['ds'], df['y']):
    #         plt.text(i, j, str(j), ha='center', va='bottom')

    #     # for model in most_model:
    #     #     plt.plot(df['ds'], df[model], label=model,marker='o')
    #     # 当前日期画竖虚线
    #     plt.axvline(x=df['ds'].iloc[-horizon], color='r', linestyle='--')
    #     plt.legend()
    #     plt.xlabel('日期')
    #     plt.ylabel('价格')
        
    #     plt.savefig(os.path.join(dataset,'历史价格-预测值.png'), bbox_inches='tight')
    #     plt.close()
        
    def _plt_top10_predict_ture():
        # 模型评估前十均值画图
        df = sqlitedb.select_data(table_name = "accuracy")
        # CREAT_DATE 去重取id最大的数据
        df = df.sort_values(by=['CREAT_DATE','id'],ascending=[False,False]).drop_duplicates(subset=['CREAT_DATE'],keep='last')
        print(df.shape)
        lens = df.shape[0] if df.shape[0] < 180 else 180 
        df = df[-lens:] # 取180个数据点画图
        # 历史价格
        plt.figure(figsize=(20, 10))
        plt.plot(df['ds'], df['y'], label='真实值')
        # 均值线
        df['mean'] = df[allmodelnames[:10]].mean(axis=1)
        plt.plot(df['ds'], df['mean'], color='g', linestyle='--', label='前十模型预测均值')
        plt.plot(df['ds'], df['min_price'], color='r', linestyle='--', label='min_price')
        plt.plot(df['ds'], df['max_price'], color='r', linestyle='--', label='max_price')
        # 颜色填充
        plt.fill_between(df['ds'], df['max_price'], df['min_price'], alpha=0.2)
        markers = ['o', 's', '^', 'D', 'v', '*', 'p', 'h', 'H', '+', 'x', 'd']
        random_marker = random.choice(markers)
        # for model in modelnames[:5]:
        # for model in ['BiTCN','RNN']:
            # plt.plot(df['ds'][-horizon:], df[model][-horizon:], label=model,marker=random_marker)
        # plt.plot(df_combined3['ds'], df_combined3['min_abs_error_rate_prediction'], label='最小绝对误差', linestyle='--', color='orange')
        # 网格
        plt.grid(True)
        # 显示历史值
        # for i, j in zip(df['ds'], df['y']):
        #     plt.text(i, j, str(j), ha='center', va='bottom')

        # for model in most_model:
        #     plt.plot(df['ds'], df[model], label=model,marker='o')
        # 当前日期画竖虚线
        plt.axvline(x=df['ds'].iloc[-horizon], color='r', linestyle='--')
        plt.legend()
        plt.xlabel('日期')
        plt.ylabel('价格')
        
        plt.savefig(os.path.join(dataset,'历史价格-预测值1.png'), bbox_inches='tight')
        plt.close()

    def _plt_predict_table(df): 
        # 预测值表格
        fig, ax = plt.subplots(figsize=(20, 6))
        ax.axis('off')  # 关闭坐标轴
        # 数值保留2位小数
        df = df.round(2)
        df = df[-horizon:]
        df['Day'] = [f'Day_{i}' for i in range(1,horizon+1)]
        # Day列放到最前面
        df = df[['Day'] + list(df.columns[:-1])]
        table = ax.table(cellText=df.values, colLabels=df.columns, loc='center')
        #加宽表格
        table.auto_set_font_size(False)
        table.set_fontsize(10)

        # 设置表格样式，列数据最小的用绿色标识
        plt.savefig(os.path.join(dataset,'预测值表格.png'), bbox_inches='tight')
        plt.close()
       
    def _plt_model_results3():
        # 可视化评估结果
        plt.rcParams['font.sans-serif'] = ['SimHei']
        fig, ax = plt.subplots(figsize=(20, 10))
        ax.axis('off')  # 关闭坐标轴
        table = ax.table(cellText=model_results3.values, colLabels=model_results3.columns, loc='center')
        # 加宽表格
        table.auto_set_font_size(False)
        table.set_fontsize(10)

        # 设置表格样式，列数据最小的用绿色标识
        plt.savefig(os.path.join(dataset,'模型评估.png'), bbox_inches='tight')
        plt.close()

    # _plt_predict_ture(df_combined3)
    _plt_top10_predict_ture()
    _plt_predict_table(df_combined3)
    _plt_model_results3()

    return model_results3
 
model_losss(sqlitedb=sqlitedb,end_time='2024-12-16')

(51, 30)


模型(Model)  平均平方误差(MSE)  均方根误差(RMSE)  平均绝对误差(MAE)
11       DilatedRNN     1.567000        1.252        0.978
14          NLinear     1.905000        1.380        1.104
10            BiTCN     1.906000        1.380        1.042
6          PatchTST     1.939000        1.393        1.129
19             TiDE     1.967000        1.402        1.090
4           TSMixer     2.056000        1.434        1.111
7               RNN     2.101000        1.449        1.144
13          DLinear     2.162000        1.470        1.178
15              TFT     2.196000        1.482        1.137
16        FEDformer     2.211000        1.487        1.239
9               TCN     2.397000        1.548        1.276
0             NHITS     2.454000        1.567        1.190
12              MLP     2.468000        1.571        1.224
5          TSMixerx     2.490000        1.578        1.231
1          Informer     3.095000        1.759        1.352
20         DeepNPTS     3.267000        1.808        1.357
8               GRU     5.172000        2.274        1.909
2              LSTM     6.844000        2.616        2.386
18  MLPMultivariate     8.163000        2.857        2.221
17          StemGNN    17.216000        4.149        3.359
3      iTransformer    21.568001        4.644        3.487